In [1]:
import os
import cv2
import copy
import numpy as np
import tensorflow as tf
from tensorflow import keras
import matplotlib.pyplot as plt
from keras import layers, utils, models, callbacks as cb
from sklearn.metrics import ConfusionMatrixDisplay, confusion_matrix
import scipy.stats as st
np.set_printoptions(threshold=np.inf)

In [41]:
methods = [cv2.NORM_HAMMING, cv2.NORM_HAMMING2, cv2.NORM_L1, cv2.NORM_L2, cv2.NORM_L2SQR, cv2.NORM_TYPE_MASK]
method_names = { 
    cv2.NORM_HAMMING: "cv2.NORM_HAMMING",
    cv2.NORM_HAMMING2: "cv2.NORM_HAMMING2",
    cv2.NORM_L1: "cv2.NORM_L1",
    cv2.NORM_L2: "cv2.NORM_L2",
    cv2.NORM_L2SQR: "cv2.NORM_L2SQR",
    cv2.NORM_RELATIVE: "cv2.NORM_RELATIVE",
    cv2.NORM_RELATIVE: "cv2.NORM_RELATIVE",
    cv2.NORM_TYPE_MASK: "cv2.NORM_TYPE_MASK",
}

def align(img: np.array, template: np.array) -> np.array:
    original = img
    original_template = template

    # img = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    # template = cv2.cvtColor(template, cv2.COLOR_BGR2GRAY)

    height, width, _ = template.shape
    
    # Create ORB detector with 5000 features.
    orb_detector = cv2.ORB_create(20000)
    
    # Find keypoints and descriptors.
    # The first arg is the image, second arg is the mask
    #  (which is not required in this case).
    kp1, d1 = orb_detector.detectAndCompute(img, None)
    kp2, d2 = orb_detector.detectAndCompute(template, None)
    
    # Match features between the two images.
    # We create a Brute Force matcher with
    # Hamming distance as measurement mode.

    results = []

    for method in methods:
        matcher = cv2.BFMatcher(method, crossCheck = True)
        
        # Match the two sets of descriptors.
        try:
            matches = matcher.match(d1, d2)
        except:
            print(f'{method_names[method]} failed.')
            continue        
        # Sort matches on the basis of their Hamming distance.
        
        # print(f'{matches=}')
        # print(f'{type(matches)=}')

        matches = sorted(matches, key = lambda x: x.distance)
        # Take the top 90 % matches forward.
        matches = matches[:int(len(matches)*0.9)]
        no_of_matches = len(matches)
        
        # Define empty matrices of shape no_of_matches * 2.
        p1 = np.zeros((no_of_matches, 2))
        p2 = np.zeros((no_of_matches, 2))
        
        for i in range(len(matches)):
            p1[i, :] = kp1[matches[i].queryIdx].pt
            p2[i, :] = kp2[matches[i].trainIdx].pt
        
        # Find the homography matrix.
        homography, mask = cv2.findHomography(p1, p2, cv2.RANSAC)
        
        # Use this matrix to transform the
        # colored image wrt the reference image.

        result =  cv2.warpPerspective(
            original,
            homography, (width, height)
        )

        if result.shape == template.shape:
            results.append(result)
        else:
            print(f'{method_names[method]} did not produce the same shape')
    
    best = None
    best_sum = None
    for image in results:
        diff = cv2.absdiff(image, original_template)
        delta = np.sum(diff)
        if best is None or delta < best_sum:
            best = image
            best_sum = delta
    return best

In [42]:
# methods = [cv2.NORM_HAMMING, cv2.NORM_HAMMING2, cv2.NORM_L1, cv2.NORM_L2, cv2.NORM_L2SQR, cv2.NORM_RELATIVE, cv2.NORM_RELATIVE, cv2.NORM_TYPE_MASK]

# def align(img: np.array, template: np.array) -> np.array:
#     original = img
    
#     img = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
#     template = cv2.cvtColor(template, cv2.COLOR_BGR2GRAY)

#     height, width = template.shape
    
#     # Create ORB detector with 5000 features.
#     orb_detector = cv2.ORB_create(5000)
    
#     # Find keypoints and descriptors.
#     # The first arg is the image, second arg is the mask
#     #  (which is not required in this case).
#     kp1, d1 = orb_detector.detectAndCompute(img, None)
#     kp2, d2 = orb_detector.detectAndCompute(template, None)
    
#     # Match features between the two images.
#     # We create a Brute Force matcher with
#     # Hamming distance as measurement mode.

#     matcher = cv2.BFMatcher(methods[1], crossCheck = True)
    
#     # Match the two sets of descriptors.
#     matches = matcher.match(d1, d2)
    
#     # Sort matches on the basis of their Hamming distance.
    
#     # print(f'{matches=}')
#     # print(f'{type(matches)=}')

#     matches = sorted(matches, key = lambda x: x.distance)
#     # Take the top 90 % matches forward.
#     matches = matches[:int(len(matches)*0.9)]
#     no_of_matches = len(matches)
    
#     # Define empty matrices of shape no_of_matches * 2.
#     p1 = np.zeros((no_of_matches, 2))
#     p2 = np.zeros((no_of_matches, 2))
    
#     for i in range(len(matches)):
#         p1[i, :] = kp1[matches[i].queryIdx].pt
#         p2[i, :] = kp2[matches[i].trainIdx].pt
    
#     # Find the homography matrix.
#     homography, mask = cv2.findHomography(p1, p2, cv2.RANSAC)
    
#     # Use this matrix to transform the
#     # colored image wrt the reference image.
#     return cv2.warpPerspective(
#         original,
#         homography, (width, height)
#     )

In [43]:
def align_and_subtract(img: np.array, template: np.array) -> np.array:
    reg = align(img, template)
    return reg, cv2.subtract(reg, template)

In [44]:
def generate_template_from(root: list[str]):
    imgs = [cv2.imread(imgpath) for imgpath in root]
    for x in imgs:
        print(x.shape)
    
    print(len(imgs)-1)
    template = st.tmax(imgs, upperlimit=255, inclusive=False)
    assert template.shape == imgs[0].shape

    # display(template)
    # display(cv2.subtract(imgs[0], template))
    
    return template


In [45]:
# docid = "svk_id"
# doctype = os.path.join(os.getcwd(), "datasets", "midv-2020", docid)
# scanned_doctype = os.path.join(os.getcwd(), "datasets", "midv-2020-scanned", docid)


In [46]:
# import os

# template = cv2.imread(os.path.join(doctype, "base_template.bmp"))
# root = r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\svk_id\original_genuine"
# files = []

# # if not os.path.isdir(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\svk_id\unaligned_genuines"):
# #     os.mkdir(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\svk_id\unaligned_genuines")

# for file in os.listdir(root):
#     filepath = os.path.join(root, file)
#     files.append(filepath)

# template = generate_template_from(files)
# cv2.imwrite(f'E:\\University\\Semester 6\\Grad\\forgery detection\\forgery detection neural network\\datasets\\midv-2020-scanned\\svk_id\\aligned_template.bmp', template)


In [47]:
import os
import cv2
from PIL import Image
docid= "srb_passport"
# doctype = os.path.join(os.getcwd(), "datasets", "midv-2020", docid)
alligned_doctype = os.path.join(os.getcwd(), "datasets", "midv-2020-scanned",docid)
template = cv2.imread(os.path.join(alligned_doctype, "aligned_template.bmp"))


root = f'E:\\University\\Semester 6\\Grad\\forgery detection\\forgery detection neural network\\datasets\\midv-2020-scanned\\{docid}\\unaligned forgeries'
for x in os.listdir(root):
    y = os.path.join(root, x)
    with Image.open(y) as img:
       real = cv2.imread(y)
       real = align(real,template)
       save_path = os.path.join(alligned_doctype,'original_forged',x)
       print(save_path)
       cv2.imwrite(save_path,real)
    #    plt.imshow(cv2.cvtColor(real, cv2.COLOR_BGR2RGB))
    #    print(x)
       


e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\02.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\03.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\04.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\05.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\07.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forged\101.bmp
e:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\original_forge

In [2]:
real = cv2.imread(r"D:\Downloads\dataset\images\00.jpg")
# forged = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\alb_id\original_forged\09.png")

template = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\base_template.bmp")
# perfect_template =cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020\alb_id\base_template.bmp")

# real1 = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\alb_id\original_genuine\09.bmp")
# real2 = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\alb_id\original_forged\09.png")


# # reg_real = align(real,template)
# # reg_forged = align(forged,template)
diff_real = cv2.subtract(real,template)
# diff_forged = cv2.subtract(forged,template)

# diff_perfect_real = cv2.subtract(real,perfect_template)

# diff_perfect_forged = cv2.subtract(forged,perfect_template)

# diff_perfect_real_forged = cv2.subtract(diff_perfect_real, diff_perfect_forged)

cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_real.bmp',diff_real)
# cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_forged.bmp',diff_forged)
# cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_perfect_real.bmp',diff_perfect_real)
# cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_perfect_forged.bmp',diff_perfect_forged)
# cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_perfect_real_forged.bmp',diff_perfect_real_forged)


# # cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff_forged_temp2.bmp',diff_forged)
# # subtract_real_forged = cv2.absdiff(diff_real,diff_forged)
# # cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\subtract_real_forged_temp2.bmp',subtract_real_forged)
# # reg = align(img, template)
# # print(reg.shape)
# # print(template.shape)
# # plt.imshow(cv2.cvtColor(reg_forged, cv2.COLOR_BGR2RGB))
# # plt.show()
# # plt.imshow(cv2.cvtColor(cv2.subtract(reg,template), cv2.COLOR_BGR2RGB))
# # diff=cv2.subtract(reg,template)
# # cv2.imwrite(r'D:\Downloads\dataset\scan_rotated\images\diff2.bmp',diff)
# # plt.show()

True

In [49]:
real1 = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020\srb_passport\validation\genuine\04.bmp")
real2 = cv2.imread(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\experiment 2\alb_id\aligned_template.bmp")
print(real1)
# print(real2)
subtract_reals = cv2.subtract(real1,real2)
# print(subtract_reals)

[[[0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]
  [0 0 0]


In [50]:
# bmp1 = cv2.imread()
# bmp2 = cv2.imread(r"")
with Image.open(r"E:\University\Semester 6\Grad\forgery detection\forgery detection neural network\datasets\midv-2020-scanned\srb_passport\75.bmp") as img:
        print(f'{img.mode}')


RGB
